## Loading Features (with generic numpy loading function) & Parcellations (with ci_lib package)

#### Imports

In [6]:
# Loading 
from pathlib import Path
from os import path
import sys
from os import listdir
from os.path import isfile, join

# Custom library from WIPAR
sys.path.append(str((Path.cwd().parent))) #use local version of ci_lib during development
import ci_lib
from ci_lib.utils import snakemake_tools
from ci_lib.features import Features, Means, Raws, Covariances, AutoCovariances, Moup, AutoCorrelations, Feature_Type
from ci_lib.plotting import graph_circle_plot, plot_glassbrain_bokeh, draw_neural_activity
from ci_lib import DecompData
from ci_lib.feature_selection import RFE_pipeline
from ci_lib.networks import construct_network, construct_network_from_feat, add_bokeh_attributes

# Processing
import numpy as np
import networkx as nx

# Dict Formating
import json     
import collections
import pandas as pd

# Plotting
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go


In [10]:
#Helper functions
def print_dict_keys(print_dict,level=0):
    if type(print_dict) is dict:
        print(f"Level {level}:",end=" ")
        print(list(print_dict.keys()))
        print_dict_keys(next(iter(print_dict.values())),level+1)
    else:
        print(f"Example shape of Value (feature): {print_dict.shape}")

#Used to get session name on last dim
def get_key_last_dim(rec_dict):
    #Look one level ahead
    arbitary_next_dict = next(iter(rec_dict.values()))

    if type(arbitary_next_dict) is dict:
        #If still dict continue recursion with next element
        return get_key_last_dim(arbitary_next_dict)
    else:
        #Else return a key from current level
        return list(rec_dict.keys())[0]  #TODO this will break if 'All' becomes first entry as it has no parcellation and is only the aggregation of the features from different sessions


## Loading
* Feature Values (exported, can be loaded using generic numpy loading function)
* Parcellations to get labels of nodes (custom class, load with ci_lib package)

In [18]:
''' 
Example of loading exports from WIPAR:
    Load dictionary that aggregates Feature Values {Parcellation x Feature x Condition x  (Combined Sessions + Indivdual Sessions)}
'''

#Manually define export file for loading (otherwise most recent export is loaded)
overwrite_file= "feats_hash21d06f7c122a1207253bf0456f0a470b.npy" #None#"feats_hash24ae51c88147d75f1b297312e527fe8a.npy" #None #'feats_hashe9f3cb364387659e2448218ee96b2de8.npy' #None 

export_path = Path.cwd().parent/"results/exports/"

if overwrite_file is not None:
    #Loads manually defined export file
    loading_path = export_path/overwrite_file
else:
    #Iterates all export files to find most recent
    files = [export_path/f for f in listdir(export_path) if isfile(join(export_path, f))]
    try:
        loading_path = files[np.argmin([os.path.getmtime(f) for f in files])]

    except ValueError as err:
        if 'empty sequence' in str(err):
            print("Export folder is empty, run the feature rule first")
            loading_path = None 

#Loading
if loading_path is not None:   

    feat_dict = np.load(loading_path, allow_pickle=True)

    print(feat_dict)
    print(f"Loaded feature dict from: {loading_path}")
    print("With the following structure:")
    print_dict_keys(feat_dict)


{"anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,MOs-L,SSp-bfd-L,VISrl-L,VISp-L']": {'mean': {'leftResponse_leftStim': {'GN06.2021-03-26_10-53-05': array([[[-0.01503809, -0.01564614, -0.01327082, ..., -0.01023302,
         -0.01048999, -0.0087427 ],
        [-0.01342343, -0.0119474 , -0.0115831 , ..., -0.00480534,
         -0.00639102, -0.00709675],
        [-0.0134318 , -0.01006527, -0.00885781, ..., -0.00261249,
         -0.00500217, -0.00739451],
        ...,
        [-0.00131493,  0.00174614, -0.01323091, ..., -0.00773287,
          0.00754273,  0.002549  ],
        [ 0.01010138,  0.01201126, -0.00317859, ...,  0.00494988,
          0.02211392,  0.01638449],
        [ 0.01190497,  0.01324278, -0.00391082, ...,  0.00453147,
          0.02466646,  0.01948287]],

       [[ 0.02666909,  0.02905495,  0.00268103, ...,  0.00608295,
          0.02788038,  0.02436294],
        [ 0.02958084,  0.03311519,  0.00807539, ...,  0.01079657,
          0.0310655 ,  0.02739522],
        [ 0.02512481

In [12]:
''' 
Example of loading custom classes from WIPAR:
    Loads the DecompData object for an arbirtary session for each parcellation
'''

#Get arbitrary session from last dim of feat_dict
example_session =   Path(get_key_last_dim(feat_dict)) 

#Get list of parcellations and features
parcellations = list(feat_dict.keys())

#?
features = list(next(iter(feat_dict.values())).keys())

#Get labels for each parcellation
labels = {}
parcellation = {}

for parcellation_name in list(feat_dict.keys()):

    #Load parcellation from arbitrary session to get labels
    res_path = Path.cwd().parent /'results'
    parcellation_path = Path(res_path/example_session/Path(parcellation_name)/"data.h5")
    parcellation[parcellation_name]= DecompData.load(parcellation_path)

    labels[parcellation_name] = parcellation.spatial_labels


print(labels)

#Ignore that hashes do not match, I'll remove that as hashes of dicts/objects are just not deterministic in python

{"anatomical_ROI~['VISp-R,VISrl-R,SSp-bfd-R,MOs-R,MOs-L,SSp-bfd-L,VISrl-L,VISp-L']": array(['VISpᴿ   ', 'VISrlᴿ  ', 'SSp-bfdᴿ', 'MOsᴿ    ', 'MOsᴸ    ',
       'SSp-bfdᴸ', 'VISrlᴸ  ', 'VISpᴸ   '], dtype='<U8'), 'anatomical_ROI~[]': array(['FRPᴿ    ', 'MOpᴿ    ', 'MOsᴿ    ', 'SSp-nᴿ  ', 'SSp-bfdᴿ',
       'SSp-llᴿ ', 'SSp-mᴿ  ', 'SSp-ulᴿ ', 'SSp-trᴿ ', 'SSp-unᴿ ',
       'SSsᴿ    ', 'AUDdᴿ   ', 'AUDpᴿ   ', 'AUDpoᴿ  ', 'AUDvᴿ   ',
       'VISalᴿ  ', 'VISamᴿ  ', 'VISlᴿ   ', 'VISpᴿ   ', 'VISplᴿ  ',
       'VISpmᴿ  ', 'VISliᴿ  ', 'VISporᴿ ', 'ACAdᴿ   ', 'PLᴿ     ',
       'RSPaglᴿ ', 'RSPdᴿ   ', 'RSPvᴿ   ', 'VISaᴿ   ', 'VISrlᴿ  ',
       'TEaᴿ    ', 'MOBᴿ    ', 'MOBᴸ    ', 'TEaᴸ    ', 'VISrlᴸ  ',
       'VISaᴸ   ', 'RSPvᴸ   ', 'RSPdᴸ   ', 'RSPaglᴸ ', 'PLᴸ     ',
       'ACAdᴸ   ', 'VISporᴸ ', 'VISliᴸ  ', 'VISpmᴸ  ', 'VISplᴸ  ',
       'VISpᴸ   ', 'VISlᴸ   ', 'VISamᴸ  ', 'VISalᴸ  ', 'AUDvᴸ   ',
       'AUDpoᴸ  ', 'AUDpᴸ   ', 'AUDdᴸ   ', 'SSsᴸ    ', 'SSp-unᴸ ',
       'SSp-trᴸ ', 'SSp-ulᴸ ', '

In [ ]:
#Plot neural activity in spatial dimension

frame = 
draw_neural_activity()
